In [14]:
# BASE
# ------------------------------------------------------
import numpy as np
import pandas as pd
import os
import gc
import warnings

# PACF - ACF
# ------------------------------------------------------
import statsmodels.api as sm

# DATA VISUALIZATION
# ------------------------------------------------------
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px


# CONFIGURATIONS
# ------------------------------------------------------
pd.set_option('display.max_columns', None)
pd.options.display.float_format = '{:.2f}'.format
warnings.filterwarnings('ignore')

In [13]:
!pip install numpy
!pip install pandas
!pip install plotly
!pip install statsmodels
!pip install matplotlib
!pip install seaborn

You should consider upgrading via the '/Users/ben/venv/bin/python -m pip install --upgrade pip' command.
You should consider upgrading via the '/Users/ben/venv/bin/python -m pip install --upgrade pip' command.
You should consider upgrading via the '/Users/ben/venv/bin/python -m pip install --upgrade pip' command.
You should consider upgrading via the '/Users/ben/venv/bin/python -m pip install --upgrade pip' command.
You should consider upgrading via the '/Users/ben/venv/bin/python -m pip install --upgrade pip' command.
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 285.1/285.1 KB 2.9 MB/s eta 0:00:00a 0:00:01
You should consider upgrading via the '/Users/ben/venv/bin/python -m pip install --upgrade pip' command.


## 1. Import Data

In [7]:
train = pd.read_csv('data/train.csv)
test = pd.read_csv('data/test.csv')
stores = pd.read_csv('data/stores.csv')
transactions = pd.read_csv('data/transactions.csv')
transactions = transactions.sort_values(['store_nbr', 'date'])

In [16]:
train.head()

id        date  store_nbr      family  sales  onpromotion
0   0  2013-01-01          1  AUTOMOTIVE   0.00            0
1   1  2013-01-01          1   BABY CARE   0.00            0
2   2  2013-01-01          1      BEAUTY   0.00            0
3   3  2013-01-01          1   BEVERAGES   0.00            0
4   4  2013-01-01          1       BOOKS   0.00            0

In [17]:
type(train['date'][0])

str

In [18]:
# Datetime
train['date'] = pd.to_datetime(train.date)

In [19]:
type(train['date'][0])

pandas._libs.tslibs.timestamps.Timestamp

In [20]:
test['date'] = pd.to_datetime(test.date)
transactions['date'] = pd.to_datetime(transactions.date)

In [21]:
train.onpromotion

0            0
1            0
2            0
3            0
4            0
          ... 
3000883      0
3000884      1
3000885    148
3000886      8
3000887      0
Name: onpromotion, Length: 3000888, dtype: int64

In [22]:
# data types
train.onpromotion = train.onpromotion.astype('float16')
train.sales = train.sales.astype('float32')
stores.cluster = stores.cluster.astype('int8')
train.head()

id       date  store_nbr      family  sales  onpromotion
0   0 2013-01-01          1  AUTOMOTIVE   0.00         0.00
1   1 2013-01-01          1   BABY CARE   0.00         0.00
2   2 2013-01-01          1      BEAUTY   0.00         0.00
3   3 2013-01-01          1   BEVERAGES   0.00         0.00
4   4 2013-01-01          1       BOOKS   0.00         0.00

## 2. Transactions

In [23]:
transactions.head(10)

date  store_nbr  transactions
1   2013-01-02          1          2111
47  2013-01-03          1          1833
93  2013-01-04          1          1863
139 2013-01-05          1          1509
185 2013-01-06          1           520
231 2013-01-07          1          1807
277 2013-01-08          1          1869
323 2013-01-09          1          1910
369 2013-01-10          1          1679
415 2013-01-11          1          1813

In [24]:
# aggregate
train_agg = train.groupby(['date', 'store_nbr']).sales.sum().reset_index()
train_agg.head()

date  store_nbr  sales
0 2013-01-01          1   0.00
1 2013-01-01          2   0.00
2 2013-01-01          3   0.00
3 2013-01-01          4   0.00
4 2013-01-01          5   0.00

In [25]:
temp = pd.merge(train_agg, transactions, how = 'left')
temp.head()

date  store_nbr  sales  transactions
0 2013-01-01          1   0.00           NaN
1 2013-01-01          2   0.00           NaN
2 2013-01-01          3   0.00           NaN
3 2013-01-01          4   0.00           NaN
4 2013-01-01          5   0.00           NaN

In [26]:
print("Spearman Correlation between Total Sales and Transactions: {:,.4f}".format(temp.corr('spearman').sales.loc['transactions']))

Spearman Correlation between Total Sales and Transactions: 0.8175


In [27]:
px.line(transactions.sort_values(['store_nbr', 'date']), x='date', y='transactions', color='store_nbr', title='Transactions')